In [1]:
from nes_py.wrappers import JoypadSpace
import gym_super_mario_bros
from gym_super_mario_bros.actions import SIMPLE_MOVEMENT
import numpy as np 
env = gym_super_mario_bros.make('SuperMarioBros-v0', apply_api_compatibility=True, render_mode="human")
env = JoypadSpace(env, SIMPLE_MOVEMENT)


/home/edu/anaconda3/envs/tp_ap/lib/python3.9/site-packages/gym/envs/registration.py:555: UserWarning: WARN: The environment SuperMarioBros-v0 is out of date. You should consider upgrading to version `v3`.
  logger.warn(
/home/edu/anaconda3/envs/tp_ap/lib/python3.9/site-packages/gym/envs/registration.py:627: UserWarning: WARN: The environment creator metadata doesn't include `render_modes`, contains: ['render.modes', 'video.frames_per_second']
  logger.warn(


In [2]:
from gym.spaces import Box
from gym import Wrapper, ObservationWrapper
from gym.wrappers import FrameStack, GrayScaleObservation, ResizeObservation

class CustomWrapper(Wrapper):
    def reset(self, **kwargs):
        kwargs.pop('seed', None)  # Remove the 'seed' argument
        kwargs.pop('options', None)  # Remove the 'options' argument
        return self.env.reset(**kwargs)

# Wrap your environment
env = CustomWrapper(env)

class SkipFrame(Wrapper):
    def __init__(self, env, skip):
        """Return only every `skip`-th frame"""
        super().__init__(env)
        self._skip = skip

    def step(self, action):
        """Repeat action, and sum reward"""
        total_reward = 0.0
        for i in range(self._skip):
            # Accumulate reward and repeat the same action
            obs, reward, done, trunk, info = self.env.step(action)
            total_reward += reward
            if done:
                break
        return obs, total_reward, done, trunk, info

    
class RemoveChannelDim(ObservationWrapper):
    def observation(self, observation):
        return np.squeeze(observation)
    
# Apply Wrappers to environment
env = SkipFrame(env, skip=4)
env = GrayScaleObservation(env)
env = ResizeObservation(env, shape=84)
env = RemoveChannelDim(env)
env = FrameStack(env, num_stack=4)


In [3]:
from stable_baselines3 import PPO
from stable_baselines3.common.callbacks import BaseCallback
import os

2023-06-12 02:56:25.404792: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-06-12 02:56:26.422336: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [4]:
class TrainAndLoggingCallback(BaseCallback):

    def __init__(self, check_freq, save_path, verbose=1):
        super(TrainAndLoggingCallback, self).__init__(verbose)
        self.check_freq = check_freq
        self.save_path = save_path

    def _init_callback(self):
        if self.save_path is not None:
            os.makedirs(self.save_path, exist_ok=True)

    def _on_step(self):
        if self.n_calls % self.check_freq == 0:
            model_path = os.path.join(self.save_path, 'best_model_{}'.format(self.n_calls))
            self.model.save(model_path)

        return True

In [5]:
CHECKPOINT_DIR = './ppo/train/'
LOG_DIR = './ppo/logs/'

In [6]:
# Setup model saving callback
callback = TrainAndLoggingCallback(check_freq=250000, save_path=CHECKPOINT_DIR)

In [7]:
import torch as th
import torch.nn as nn
from gymnasium import spaces

from stable_baselines3 import PPO
from stable_baselines3.common.torch_layers import BaseFeaturesExtractor


class CustomCNN(BaseFeaturesExtractor):
    """
    :param observation_space: (gym.Space)
    :param features_dim: (int) Number of features extracted.
        This corresponds to the number of unit for the last layer.
    """

    def __init__(self, observation_space: spaces.Box, features_dim: int = 256):
        super().__init__(observation_space, features_dim)
        # We assume CxHxW images (channels first)
        # Re-ordering will be done by pre-preprocessing or wrapper
        n_input_channels = observation_space.shape[0]
        self.cnn = nn.Sequential(
            nn.Conv2d(in_channels=n_input_channels, out_channels=32, kernel_size=8, stride=4),
            nn.ReLU(),
            nn.Conv2d(in_channels=32, out_channels=64, kernel_size=4, stride=2),
            nn.ReLU(),
            nn.Conv2d(in_channels=64, out_channels=64, kernel_size=3, stride=1),
            nn.ReLU(),
            nn.MaxPool2d(kernel_size=(2,2), stride=(2,2)),
            nn.Flatten(),
        )

        # Compute shape by doing one forward pass
        with th.no_grad():
            n_flatten = self.cnn(
                th.as_tensor(observation_space.sample()[None]).float()
            ).shape[1]

        self.linear = nn.Sequential(nn.Linear(576, 256),
                                    nn.ReLU(),
                                    nn.Linear(256, 128),
                                    nn.ReLU(),
                                    nn.Linear(128, features_dim), nn.Softmax(dim=1))
            #nn.Linear(n_flatten, features_dim), nn.ReLU())

    def forward(self, observations: th.Tensor) -> th.Tensor:
        return self.linear(self.cnn(observations))

policy_kwargs = dict(
    features_extractor_class=CustomCNN,
    features_extractor_kwargs=dict(features_dim=7),
)


In [8]:
model = PPO('CnnPolicy', env, verbose=1, tensorboard_log=LOG_DIR, learning_rate=0.000001, 
            n_steps=512, policy_kwargs=policy_kwargs) 


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/home/edu/anaconda3/envs/tp_ap/lib/python3.9/site-packages/stable_baselines3/common/vec_env/patch_gym.py:49: UserWarning: You provided an OpenAI Gym environment. We strongly recommend transitioning to Gymnasium environments. Stable-Baselines3 is automatically wrapping your environments in a compatibility layer, which could potentially cause issues.
  warnings.warn(


In [ ]:
from stable_baselines3.common.logger import configure

def train_model():
    env.reset()
    new_logger = configure(LOG_DIR, ["stdout", "csv"])
    # Set new logger 
    model.set_logger(new_logger)

    model.learn(total_timesteps=8000000, callback=callback)

train_model()

Logging to ./ppo/logs/
----------------------------
| time/              |     |
|    fps             | 34  |
|    iterations      | 1   |
|    time_elapsed    | 14  |
|    total_timesteps | 512 |
----------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 484          |
|    ep_rew_mean          | 1.28e+03     |
| time/                   |              |
|    fps                  | 32           |
|    iterations           | 2            |
|    time_elapsed         | 31           |
|    total_timesteps      | 1024         |
| train/                  |              |
|    approx_kl            | 8.731149e-09 |
|    clip_fraction        | 0            |
|    clip_range           | 0.2          |
|    entropy_loss         | -1.95        |
|    explained_variance   | -4.08e-05    |
|    learning_rate        | 1e-06        |
|    loss                 | 1.42e+03     |
|    n_updates            | 10           |


In [ ]:
model.save('test_model_ppo_custom_nets')

In [ ]:
#env.close()

In [ ]:
# Load model
#model = PPO.load('test_model')
## Start the game 
#state = env.reset()
#print(type(state))
#print(state)
#print(env.action_space)
#observation_shape = state[0].shape
#print(observation_shape)
## Loop through the game
#while True: 
#    action, _states = model.predict(state[0])
#    state, reward, done, info = env.step(action)
#
#    env.render()
#
#    if done:
#        state = env.reset()
#        break  # Break the loop if the game is over


from stable_baselines3.common.evaluation import evaluate_policy

model = PPO.load("ppo/train/best_model_1000000")
obs = env.reset()

#cr = 0
#while True:
#    action, _states = model.predict(obs, deterministic=False)
#    obs, rewards, done, info = env.step(action)
#    env.step(action)
#    cr += rewards
#    print("Reward: {}\t\t".format(cr), end='\r')
#    env.render()
#    if (done):
#        print("Finished an episode with total reward: ", cr)
#        cr = 0
#        break


print(evaluate_policy(model, env, n_eval_episodes=30, deterministic=False, render=True))

print("Done.")


In [ ]:
env.close()

In [ ]:
import pandas as pd

df = pd.read_csv("ppo/logs/progress.csv")
df

In [ ]:
df = df.fillna(0)
df

In [ ]:
import matplotlib.pyplot as plt
ypoints = np.array(df['rollout/ep_rew_mean'].to_numpy())
plt.plot(ypoints, color = 'b')
plt.show()

In [ ]:
from gym_super_mario_bros.actions import SIMPLE_MOVEMENT

SIMPLE_MOVEMENT

In [ ]:
env.close()